# **The Battle of Neighborhoods in New York City**

## *Segmenting and clustering neighborhoods in New York City to determine the most ideal location for a Caribbean cuisine restaurant*

## **Import dependencies**

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors
import matplotlib.pyplot as plt

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


## **Download and explore dataset**

*The dataset includes the 5 boroughs in NYC and all the neighborhoods in these boroughs and their respective latitude and longitude*

In [2]:
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

Data downloaded!


In [3]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

*Create a 'features' variable to host data*

In [4]:
newyork_data

{'type': 'FeatureCollection',
 'totalFeatures': 306,
 'features': [{'type': 'Feature',
   'id': 'nyu_2451_34572.1',
   'geometry': {'type': 'Point',
    'coordinates': [-73.84720052054902, 40.89470517661]},
   'geometry_name': 'geom',
   'properties': {'name': 'Wakefield',
    'stacked': 1,
    'annoline1': 'Wakefield',
    'annoline2': None,
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.84720052054902,
     40.89470517661,
     -73.84720052054902,
     40.89470517661]}},
  {'type': 'Feature',
   'id': 'nyu_2451_34572.2',
   'geometry': {'type': 'Point',
    'coordinates': [-73.82993910812398, 40.87429419303012]},
   'geometry_name': 'geom',
   'properties': {'name': 'Co-op City',
    'stacked': 2,
    'annoline1': 'Co-op',
    'annoline2': 'City',
    'annoline3': None,
    'annoangle': 0.0,
    'borough': 'Bronx',
    'bbox': [-73.82993910812398,
     40.87429419303012,
     -73.82993910812398,
     40.87429419303012]}},
  {'type': 'Feature',
 

In [6]:
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
neighborhoods = pd.DataFrame(columns=column_names)

In [7]:
neighborhoods_data = newyork_data['features']

In [8]:
neighborhoods_data[0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

*Loop the data and fill the 'Borough' dataframe*

In [9]:
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [10]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [11]:
print('The dataframe has {} boroughs and {} neighborhoods.'.format(
        len(neighborhoods['Borough'].unique()),
        neighborhoods.shape[0]
    )
)

The dataframe has 5 boroughs and 306 neighborhoods.


In [12]:
print(neighborhoods.Borough.unique())

['Bronx' 'Manhattan' 'Brooklyn' 'Queens' 'Staten Island']


Use *geopy* library to obtain latitude and longitude of NYC 

In [13]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7308619, -73.9871558.


## Map of NYC neighborhoods

In [14]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Use FourSquare API to explore, cluster and segment neighborhoods 

In [15]:
# define function to get venue list in neighbourhood
def getNearbyVenues(names, latitudes, longitudes):
    venues_list=[]
    CLIENT_ID = 'YXEOOWTLRQO5OH3VPQQGFL3L4N4MKFNALBHUHMFUWCUBRFFI' 
    CLIENT_SECRET = 'QXTGWBWIGBDS15ZZAIGG5BXQNPAQMPC12RR2IEQKXFXEBR2S'
    VERSION = '20180604'
    LIMIT = 100
    radius = 500
    for name, lat, lng in zip(names, latitudes, longitudes):
        # create the API request
        url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}'.format(
            CLIENT_ID, CLIENT_SECRET, lat, lng, VERSION, radius, LIMIT)
        # make the GET request
        results =requests.get(url).json()["response"]['groups'][0]['items']
        #return only names, location
        venues_list.append([(
        name, lat, lng, v['venue']['name'],v['venue']['location']['lat'],
        v['venue']['location']['lng'],    
        v['venue']['categories'][0]['name']) for v in results])
    nearby_venues =pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    return nearby_venues

## Create a dataframe for each of the 5 boroughs

In [16]:
#create a dataframe containing The Bronx borough
checked_borough ='The Bronx'
bronx_borough = neighborhoods[neighborhoods['Borough'].str.contains('Bronx')].reset_index(drop = True)
bronx_borough

Borough         Neighborhood   Latitude  Longitude
0    Bronx            Wakefield  40.894705 -73.847201
1    Bronx           Co-op City  40.874294 -73.829939
2    Bronx          Eastchester  40.887556 -73.827806
3    Bronx            Fieldston  40.895437 -73.905643
4    Bronx            Riverdale  40.890834 -73.912585
5    Bronx          Kingsbridge  40.881687 -73.902818
6    Bronx             Woodlawn  40.898273 -73.867315
7    Bronx              Norwood  40.877224 -73.879391
8    Bronx       Williamsbridge  40.881039 -73.857446
9    Bronx           Baychester  40.866858 -73.835798
10   Bronx       Pelham Parkway  40.857413 -73.854756
11   Bronx          City Island  40.847247 -73.786488
12   Bronx         Bedford Park  40.870185 -73.885512
13   Bronx   University Heights  40.855727 -73.910416
14   Bronx       Morris Heights  40.847898 -73.919672
15   Bronx              Fordham  40.860997 -73.896427
16   Bronx         East Tremont  40.842696 -73.887356
17   Bronx           West Farms  40.839475 -73.877745
18   Bronx         High  Bridge  40.836623 -73.926102
19   Bronx              Melrose  40.819754 -73.909422
20   Bronx           Mott Haven  40.806239 -73.916100
21   Bronx          Port Morris  40.801664 -73.913221
22   Bronx             Longwood  40.815099 -73.895788
23   Bronx          Hunts Point  40.809730 -73.883315
24   Bronx           Morrisania  40.823592 -73.901506
25   Bronx            Soundview  40.821012 -73.865746
26   Bronx         Clason Point  40.806551 -73.854144
27   Bronx          Throgs Neck  40.815109 -73.816350
28   Bronx         Country Club  40.844246 -73.824099
29   Bronx          Parkchester  40.837938 -73.856003
30   Bronx   Westchester Square  40.840619 -73.842194
31   Bronx             Van Nest  40.843608 -73.866299
32   Bronx          Morris Park  40.847549 -73.850402
33   Bronx              Belmont  40.857277 -73.888452
34   Bronx       Spuyten Duyvil  40.881395 -73.917190
35   Bronx      North Riverdale  40.908543 -73.904531
36   Bronx           Pelham Bay  40.850641 -73.832074
37   Bronx        Schuylerville  40.826580 -73.826203
38   Bronx       Edgewater Park  40.821986 -73.813885
39   Bronx          Castle Hill  40.819014 -73.848027
40   Bronx            Olinville  40.871371 -73.863324
41   Bronx       Pelham Gardens  40.862966 -73.841612
42   Bronx            Concourse  40.834284 -73.915589
43   Bronx            Unionport  40.829774 -73.850535
44   Bronx             Edenwald  40.884561 -73.848083
45   Bronx    Claremont Village  40.831428 -73.901199
46   Bronx    Concourse Village  40.824780 -73.915847
47   Bronx           Mount Eden  40.843826 -73.916556
48   Bronx           Mount Hope  40.848842 -73.908299
49   Bronx            Bronxdale  40.852723 -73.861726
50   Bronx             Allerton  40.865788 -73.859319
51   Bronx  Kingsbridge Heights  40.870392 -73.901523

In [17]:
#create a dataframe containing Queens borough
checked_borough ='Queens'
queens_borough = neighborhoods[neighborhoods['Borough'].str.contains('Queens')].reset_index(drop = True)
queens_borough

Borough          Neighborhood   Latitude  Longitude
0   Queens               Astoria  40.768509 -73.915654
1   Queens              Woodside  40.746349 -73.901842
2   Queens       Jackson Heights  40.751981 -73.882821
3   Queens              Elmhurst  40.744049 -73.881656
4   Queens          Howard Beach  40.654225 -73.838138
5   Queens                Corona  40.742382 -73.856825
6   Queens          Forest Hills  40.725264 -73.844475
7   Queens           Kew Gardens  40.705179 -73.829819
8   Queens         Richmond Hill  40.697947 -73.831833
9   Queens              Flushing  40.764454 -73.831773
10  Queens      Long Island City  40.750217 -73.939202
11  Queens             Sunnyside  40.740176 -73.926916
12  Queens         East Elmhurst  40.764073 -73.867041
13  Queens               Maspeth  40.725427 -73.896217
14  Queens             Ridgewood  40.708323 -73.901435
15  Queens              Glendale  40.702762 -73.870742
16  Queens             Rego Park  40.728974 -73.857827
17  Queens             Woodhaven  40.689887 -73.858110
18  Queens            Ozone Park  40.680708 -73.843203
19  Queens      South Ozone Park  40.668550 -73.809865
20  Queens         College Point  40.784903 -73.843045
21  Queens            Whitestone  40.781291 -73.814202
22  Queens               Bayside  40.766041 -73.774274
23  Queens            Auburndale  40.761730 -73.791762
24  Queens           Little Neck  40.770826 -73.738898
25  Queens            Douglaston  40.766846 -73.742498
26  Queens             Glen Oaks  40.749441 -73.715481
27  Queens             Bellerose  40.728573 -73.720128
28  Queens     Kew Gardens Hills  40.722578 -73.820878
29  Queens         Fresh Meadows  40.734394 -73.782713
30  Queens             Briarwood  40.710935 -73.811748
31  Queens        Jamaica Center  40.704657 -73.796902
32  Queens       Oakland Gardens  40.745619 -73.754950
33  Queens        Queens Village  40.718893 -73.738715
34  Queens                Hollis  40.711243 -73.759250
35  Queens         South Jamaica  40.696911 -73.790426
36  Queens            St. Albans  40.694445 -73.758676
37  Queens              Rochdale  40.675211 -73.772588
38  Queens   Springfield Gardens  40.666230 -73.760421
39  Queens       Cambria Heights  40.692775 -73.735269
40  Queens              Rosedale  40.659816 -73.735261
41  Queens          Far Rockaway  40.603134 -73.754980
42  Queens         Broad Channel  40.603027 -73.820055
43  Queens          Breezy Point  40.557401 -73.925512
44  Queens              Steinway  40.775923 -73.902290
45  Queens            Beechhurst  40.792781 -73.804365
46  Queens           Bay Terrace  40.782843 -73.776802
47  Queens              Edgemere  40.595642 -73.776133
48  Queens               Arverne  40.589144 -73.791992
49  Queens        Rockaway Beach  40.582802 -73.822361
50  Queens              Neponsit  40.572037 -73.857547
51  Queens           Murray Hill  40.764126 -73.812763
52  Queens           Floral Park  40.741378 -73.708847
53  Queens            Holliswood  40.720957 -73.767142
54  Queens       Jamaica Estates  40.716805 -73.787227
55  Queens       Queensboro Hill  40.744572 -73.825809
56  Queens             Hillcrest  40.723825 -73.797603
57  Queens            Ravenswood  40.761705 -73.931575
58  Queens            Lindenwood  40.663918 -73.849638
59  Queens             Laurelton  40.667884 -73.740256
60  Queens           Lefrak City  40.736075 -73.862525
61  Queens          Belle Harbor  40.576156 -73.854018
62  Queens         Rockaway Park  40.580343 -73.841534
63  Queens            Somerville  40.597711 -73.796648
64  Queens            Brookville  40.660003 -73.751753
65  Queens              Bellaire  40.733014 -73.738892
66  Queens          North Corona  40.754071 -73.857518
67  Queens  Forest Hills Gardens  40.714611 -73.841022
68  Queens         Jamaica Hills  40.711460 -73.796465
69  Queens                Utopia  40.733500 -73.796717
70  Queens               Pomonok  40.734936 -73.804861
71  Queens       Astoria Heights  40.770317

In [18]:
#create a dataframe containing Brooklyn borough
checked_borough ='Brooklyn'
brooklyn_borough = neighborhoods[neighborhoods['Borough'].str.contains('Brooklyn')].reset_index(drop = True)
brooklyn_borough

Borough               Neighborhood   Latitude  Longitude
0   Brooklyn                  Bay Ridge  40.625801 -74.030621
1   Brooklyn                Bensonhurst  40.611009 -73.995180
2   Brooklyn                Sunset Park  40.645103 -74.010316
3   Brooklyn                 Greenpoint  40.730201 -73.954241
4   Brooklyn                  Gravesend  40.595260 -73.973471
5   Brooklyn             Brighton Beach  40.576825 -73.965094
6   Brooklyn             Sheepshead Bay  40.586890 -73.943186
7   Brooklyn          Manhattan Terrace  40.614433 -73.957438
8   Brooklyn                   Flatbush  40.636326 -73.958401
9   Brooklyn              Crown Heights  40.670829 -73.943291
10  Brooklyn              East Flatbush  40.641718 -73.936103
11  Brooklyn                 Kensington  40.642382 -73.980421
12  Brooklyn            Windsor Terrace  40.656946 -73.980073
13  Brooklyn           Prospect Heights  40.676822 -73.964859
14  Brooklyn                Brownsville  40.663950 -73.910235
15  Brooklyn               Williamsburg  40.707144 -73.958115
16  Brooklyn                   Bushwick  40.698116 -73.925258
17  Brooklyn         Bedford Stuyvesant  40.687232 -73.941785
18  Brooklyn           Brooklyn Heights  40.695864 -73.993782
19  Brooklyn                Cobble Hill  40.687920 -73.998561
20  Brooklyn            Carroll Gardens  40.680540 -73.994654
21  Brooklyn                   Red Hook  40.676253 -74.012759
22  Brooklyn                    Gowanus  40.673931 -73.994441
23  Brooklyn                Fort Greene  40.688527 -73.972906
24  Brooklyn                 Park Slope  40.672321 -73.977050
25  Brooklyn              Cypress Hills  40.682391 -73.876616
26  Brooklyn              East New York  40.669926 -73.880699
27  Brooklyn              Starrett City  40.647589 -73.879370
28  Brooklyn                   Canarsie  40.635564 -73.902093
29  Brooklyn                  Flatlands  40.630446 -73.929113
30  Brooklyn                Mill Island  40.606336 -73.908186
31  Brooklyn            Manhattan Beach  40.577914 -73.943537
32  Brooklyn               Coney Island  40.574293 -73.988683
33  Brooklyn                 Bath Beach  40.599519 -73.998752
34  Brooklyn               Borough Park  40.633131 -73.990498
35  Brooklyn              Dyker Heights  40.619219 -74.019314
36  Brooklyn            Gerritsen Beach  40.590848 -73.930102
37  Brooklyn                Marine Park  40.609748 -73.931344
38  Brooklyn               Clinton Hill  40.693229 -73.967843
39  Brooklyn                   Sea Gate  40.576375 -74.007873
40  Brooklyn                   Downtown  40.690844 -73.983463
41  Brooklyn                Boerum Hill  40.685683 -73.983748
42  Brooklyn  Prospect Lefferts Gardens  40.658420 -73.954899
43  Brooklyn                 Ocean Hill  40.678403 -73.913068
44  Brooklyn                  City Line  40.678570 -73.867976
45  Brooklyn               Bergen Beach  40.615150 -73.898556
46  Brooklyn                    Midwood  40.625596 -73.957595
47  Brooklyn        Prospect Park South  40.647009 -73.962613
48  Brooklyn                 Georgetown  40.623845 -73.916075
49  Brooklyn          East Williamsburg  40.708492 -73.938858
50  Brooklyn                 North Side  40.714823 -73.958809
51  Brooklyn                 South Side  40.710861 -73.958001
52  Brooklyn              Ocean Parkway  40.613060 -73.968367
53  Brooklyn              Fort Hamilton  40.614768 -74.031979
54  Brooklyn                Ditmas Park  40.643675 -73.961013
55  Brooklyn                    Wingate  40.660947 -73.937187
56  Brooklyn                      Rugby  40.655572 -73.926882
57  Brooklyn             Remsen Village  40.652117 -73.916653
58  Brooklyn                   New Lots  40.662744 -73.885118
59  Brooklyn            Paerdegat Basin  40.631318 -73.902335
60  Brooklyn                 Mill Basin  40.615974 -73.915154
61  Brooklyn               Fulton Ferry  40.703281 -73.995508
62  Brooklyn               Vinegar Hill  40.703321 -73.981116
63  Brooklyn                 Weeksvil

In [19]:
#create a dataframe containing Staten Island borough
checked_borough ='Staten Island'
statenisland_borough = neighborhoods[neighborhoods['Borough'].str.contains('Staten Island')].reset_index(drop = True)
statenisland_borough

Borough       Neighborhood   Latitude  Longitude
0   Staten Island         St. George  40.644982 -74.079353
1   Staten Island       New Brighton  40.640615 -74.087017
2   Staten Island          Stapleton  40.626928 -74.077902
3   Staten Island           Rosebank  40.615305 -74.069805
4   Staten Island      West Brighton  40.631879 -74.107182
5   Staten Island        Grymes Hill  40.624185 -74.087248
6   Staten Island          Todt Hill  40.597069 -74.111329
7   Staten Island        South Beach  40.580247 -74.079553
8   Staten Island      Port Richmond  40.633669 -74.129434
9   Staten Island   Mariner's Harbor  40.632546 -74.150085
10  Staten Island         Port Ivory  40.639683 -74.174645
11  Staten Island  Castleton Corners  40.613336 -74.119181
12  Staten Island    New Springville  40.594252 -74.164960
13  Staten Island             Travis  40.586314 -74.190737
14  Staten Island           New Dorp  40.572572 -74.116479
15  Staten Island            Oakwood  40.558462 -74.121566
16  Staten Island        Great Kills  40.549480 -74.149324
17  Staten Island        Eltingville  40.542231 -74.164331
18  Staten Island           Annadale  40.538114 -74.178549
19  Staten Island            Woodrow  40.541968 -74.205246
20  Staten Island        Tottenville  40.505334 -74.246569
21  Staten Island      Tompkinsville  40.637316 -74.080554
22  Staten Island        Silver Lake  40.619193 -74.096290
23  Staten Island          Sunnyside  40.612760 -74.097126
24  Staten Island          Park Hill  40.609190 -74.080157
25  Staten Island        Westerleigh  40.621090 -74.133041
26  Staten Island       Graniteville  40.620172 -74.153152
27  Staten Island          Arlington  40.635325 -74.165104
28  Staten Island           Arrochar  40.596313 -74.067124
29  Staten Island           Grasmere  40.598268 -74.076674
30  Staten Island           Old Town  40.596329 -74.087511
31  Staten Island       Dongan Hills  40.588673 -74.096399
32  Staten Island      Midland Beach  40.573527 -74.093483
33  Staten Island         Grant City  40.576216 -74.105856
34  Staten Island     New Dorp Beach  40.564255 -74.104327
35  Staten Island        Bay Terrace  40.553988 -74.139166
36  Staten Island           Huguenot  40.531912 -74.191741
37  Staten Island    Pleasant Plains  40.524699 -74.219831
38  Staten Island       Butler Manor  40.506082 -74.229504
39  Staten Island         Charleston  40.530531 -74.232158
40  Staten Island          Rossville  40.549404 -74.215729
41  Staten Island      Arden Heights  40.549286 -74.185887
42  Staten Island         Greenridge  40.555295 -74.170794
43  Staten Island  Heartland Village  40.589139 -74.159022
44  Staten Island            Chelsea  40.594726 -74.189560
45  Staten Island         Bloomfield  40.605779 -74.187256
46  Staten Island         Bulls Head  40.609592 -74.159409
47  Staten Island      Richmond Town  40.569606 -74.134057
48  Staten Island        Shore Acres  40.609719 -74.066678
49  Staten Island            Clifton  40.619178 -74.072642
50  Staten Island            Concord  40.604473 -74.084024
51  Staten Island       Emerson Hill  40.606794 -74.097762
52  Staten Island      Randall Manor  40.635630 -74.098051
53  Staten Island       Howland Hook  40.638433 -74.186223
54  Staten Island           Elm Park  40.630147 -74.141817
55  Staten Island      Manor Heights  40.601810 -74.120594
56  Staten Island        Willowbrook  40.603707 -74.132084
57  Staten Island       Sandy Ground  40.541140 -74.217766
58  Staten Island        Egbertville  40.579119 -74.127272
59  Staten Island       Prince's Bay  40.526264 -74.201526
60  Staten Island    Lighthouse Hill  40.576506 -74.137927
61  Staten Island    Richmond Valley  40.519541 -74.229571
62  Staten Island          Fox Hills  40.617311 -74.081740

In [20]:
#create a dataframe containing Manhattan borough
checked_borough ='Manhattan'
manhattan_borough = neighborhoods[neighborhoods['Borough'].str.contains('Manhattan')].reset_index(drop = True)
manhattan_borough

Borough         Neighborhood   Latitude  Longitude
0   Manhattan          Marble Hill  40.876551 -73.910660
1   Manhattan            Chinatown  40.715618 -73.994279
2   Manhattan   Washington Heights  40.851903 -73.936900
3   Manhattan               Inwood  40.867684 -73.921210
4   Manhattan     Hamilton Heights  40.823604 -73.949688
5   Manhattan       Manhattanville  40.816934 -73.957385
6   Manhattan       Central Harlem  40.815976 -73.943211
7   Manhattan          East Harlem  40.792249 -73.944182
8   Manhattan      Upper East Side  40.775639 -73.960508
9   Manhattan            Yorkville  40.775930 -73.947118
10  Manhattan           Lenox Hill  40.768113 -73.958860
11  Manhattan     Roosevelt Island  40.762160 -73.949168
12  Manhattan      Upper West Side  40.787658 -73.977059
13  Manhattan       Lincoln Square  40.773529 -73.985338
14  Manhattan              Clinton  40.759101 -73.996119
15  Manhattan              Midtown  40.754691 -73.981669
16  Manhattan          Murray Hill  40.748303 -73.978332
17  Manhattan              Chelsea  40.744035 -74.003116
18  Manhattan    Greenwich Village  40.726933 -73.999914
19  Manhattan         East Village  40.727847 -73.982226
20  Manhattan      Lower East Side  40.717807 -73.980890
21  Manhattan              Tribeca  40.721522 -74.010683
22  Manhattan         Little Italy  40.719324 -73.997305
23  Manhattan                 Soho  40.722184 -74.000657
24  Manhattan         West Village  40.734434 -74.006180
25  Manhattan     Manhattan Valley  40.797307 -73.964286
26  Manhattan  Morningside Heights  40.808000 -73.963896
27  Manhattan             Gramercy  40.737210 -73.981376
28  Manhattan    Battery Park City  40.711932 -74.016869
29  Manhattan   Financial District  40.707107 -74.010665
30  Manhattan        Carnegie Hill  40.782683 -73.953256
31  Manhattan                 Noho  40.723259 -73.988434
32  Manhattan         Civic Center  40.715229 -74.005415
33  Manhattan        Midtown South  40.748510 -73.988713
34  Manhattan         Sutton Place  40.760280 -73.963556
35  Manhattan           Turtle Bay  40.752042 -73.967708
36  Manhattan           Tudor City  40.746917 -73.971219
37  Manhattan      Stuyvesant Town  40.731000 -73.974052
38  Manhattan             Flatiron  40.739673 -73.990947
39  Manhattan         Hudson Yards  40.756658 -74.000111

## Find *venues* per borough for modeling

In [21]:
import requests
#run function with The Bronx borough
bronx_venues = getNearbyVenues(names = bronx_borough['Neighborhood'],latitudes = bronx_borough['Latitude'], longitudes =bronx_borough['Longitude'])
bronx_venues

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0               Wakefield              40.894705              -73.847201   
1               Wakefield              40.894705              -73.847201   
2               Wakefield              40.894705              -73.847201   
3               Wakefield              40.894705              -73.847201   
4               Wakefield              40.894705              -73.847201   
5               Wakefield              40.894705              -73.847201   
6               Wakefield              40.894705              -73.847201   
7               Wakefield              40.894705              -73.847201   
8              Co-op City              40.874294              -73.829939   
9              Co-op City              40.874294              -73.829939   
10             Co-op City              40.874294              -73.829939   
11             Co-op City              40.874294              -73.829939   
12             Co-op City              40.874294              -73.829939   
13             Co-op City              40.874294              -73.829939   
14             Co-op City              40.874294              -73.829939   
15             Co-op City              40.874294              -73.829939   
16             Co-op City              40.874294              -73.829939   
17             Co-op City              40.874294              -73.829939   
18             Co-op City              40.874294              -73.829939   
19             Co-op City              40.874294              -73.829939   
20             Co-op City              40.874294              -73.829939   
21             Co-op City              40.874294              -73.829939   
22             Co-op City              40.874294              -73.829939   
23             Co-op City              40.874294              -73.829939   
24            Eastchester              40.887556              -73.827806   
25            Eastchester              40.887556              -73.827806   
26            Eastchester              40.887556              -73.827806   
27            Eastchester              40.887556              -73.827806   
28            Eastchester              40.887556              -73.827806   
29            Eastchester              40.887556              -73.827806   
30            Eastchester              40.887556              -73.827806   
31            Eastchester              40.887556              -73.827806   
32            Eastchester              40.887556              -73.827806   
33            Eastchester              40.887556              -73.827806   
34            Eastchester              40.887556              -73.827806   
35            Eastchester              40.887556              -73.827806   
36            Eastchester              40.887556              -73.827806   
37            Eastchester              40.887556              -73.827806   
38            Eastchester              40.887556              -73.827806   
39            Eastchester              40.887556              -73.827806   
40            Eastchester              40.887556              -73.827806   
41            Eastchester              40.887556              -73.827806   
42            Eastchester              40.887556              -73.827806   
43              Fieldston              40.895437              -73.905643   
44              Fieldston              40.895437              -73.905643   
45              Fieldston              40.895437              -73.905643   
46              Riverdale              40.890834              -73.912585   
47              Riverdale              40.890834              -73.912585   
48              Riverdale              40.890834              -73.912585   
49              Riverdale              40.890834              -73.912585   
50              Riverdale              40.890834              -73.912585   
51              Riverdale              40.890834             

In [22]:
bronx_venues.groupby('Venue Category').count()

Neighborhood  Neighborhood Latitude  \
Venue Category                                                       
Accessories Store                         1                      1   
African Restaurant                        2                      2   
Airport Tram                              2                      2   
American Restaurant                      13                     13   
Antique Shop                              1                      1   
Arcade                                    1                      1   
Arepa Restaurant                          1                      1   
Art Gallery                               3                      3   
Art Museum                                1                      1   
Asian Restaurant                          8                      8   
BBQ Joint                                 3                      3   
Bagel Shop                                2                      2   
Bakery                                   20                     20   
Bank                                     30                     30   
Bar                                      16                     16   
Baseball Field                            5                      5   
Basketball Court                          4                      4   
Beach                                     1                      1   
Beer Bar                                  1                      1   
Boat or Ferry                             2                      2   
Bookstore                                 1                      1   
Bowling Alley                             2                      2   
Breakfast Spot                            6                      6   
Brewery                                   1                      1   
Buffet                                    1                      1   
Building                                  1                      1   
Burger Joint                              6                      6   
Bus Line                                  1                      1   
Bus Station                              36                     36   
Bus Stop                                  9                      9   
Business Service                          2                      2   
Café                                     12                     12   
Candy Store                               1                      1   
Caribbean Restaurant                     15                     15   
Check Cashing Service                     4                      4   
Cheese Shop                               1                      1   
Chinese Restaurant                       44                     44   
Clothing Store                            6                      6   
Coffee Shop                              16                     16   
Comfort Food Restaurant                   1                      1   
Convenience Store                         9                      9   
Cosmetics Shop                            9                      9   
Cupcake Shop                              1                      1   
Dance Studio                              2                      2   
Deli / Bodega                            56                     56   
Department Store                          5                      5   
Dessert Shop                              5                      5   
Diner                                    21                     21   
Discount Store                           21                     21   
Distillery                                1                      1   
Dive Bar                                  1                      1   
Donut Shop                               41                     41   
Eastern European Restaurant               1                      1   
Electronics Store                         6                      6   
Eye Doctor                                1                      1   
Farmers Market                           

In [23]:
bronx_venues.groupby('Venue Category')['Venue'].count().sort_values(ascending=False)

Venue Category
Pizza Place                      99
Deli / Bodega                    56
Chinese Restaurant               44
Pharmacy                         41
Donut Shop                       41
Italian Restaurant               40
Supermarket                      38
Sandwich Place                   36
Bus Station                      36
Spanish Restaurant               33
Bank                             30
Fast Food Restaurant             30
Mexican Restaurant               28
Grocery Store                    24
Park                             23
Diner                            21
Discount Store                   21
Bakery                           20
Fried Chicken Joint              19
Latin American Restaurant        19
Ice Cream Shop                   17
Bar                              16
Coffee Shop                      16
Playground                       15
Caribbean Restaurant             15
Gym / Fitness Center             13
Liquor Store                     13
Shoe Store   

In [24]:
import requests
#run function with the Queens borough
queens_venues = getNearbyVenues(names = queens_borough['Neighborhood'],latitudes = queens_borough['Latitude'], longitudes =queens_borough['Longitude'])
queens_venues

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                  Astoria              40.768509              -73.915654   
1                  Astoria              40.768509              -73.915654   
2                  Astoria              40.768509              -73.915654   
3                  Astoria              40.768509              -73.915654   
4                  Astoria              40.768509              -73.915654   
5                  Astoria              40.768509              -73.915654   
6                  Astoria              40.768509              -73.915654   
7                  Astoria              40.768509              -73.915654   
8                  Astoria              40.768509              -73.915654   
9                  Astoria              40.768509              -73.915654   
10                 Astoria              40.768509              -73.915654   
11                 Astoria              40.768509              -73.915654   
12                 Astoria              40.768509              -73.915654   
13                 Astoria              40.768509              -73.915654   
14                 Astoria              40.768509              -73.915654   
15                 Astoria              40.768509              -73.915654   
16                 Astoria              40.768509              -73.915654   
17                 Astoria              40.768509              -73.915654   
18                 Astoria              40.768509              -73.915654   
19                 Astoria              40.768509              -73.915654   
20                 Astoria              40.768509              -73.915654   
21                 Astoria              40.768509              -73.915654   
22                 Astoria              40.768509              -73.915654   
23                 Astoria              40.768509              -73.915654   
24                 Astoria              40.768509              -73.915654   
25                 Astoria              40.768509              -73.915654   
26                 Astoria              40.768509              -73.915654   
27                 Astoria              40.768509              -73.915654   
28                 Astoria              40.768509              -73.915654   
29                 Astoria              40.768509              -73.915654   
30                 Astoria              40.768509              -73.915654   
31                 Astoria              40.768509              -73.915654   
32                 Astoria              40.768509              -73.915654   
33                 Astoria              40.768509              -73.915654   
34                 Astoria              40.768509              -73.915654   
35                 Astoria              40.768509              -73.915654   
36                 Astoria              40.768509              -73.915654   
37                 Astoria              40.768509              -73.915654   
38                 Astoria              40.768509              -73.915654   
39                 Astoria              40.768509              -73.915654   
40                 Astoria              40.768509              -73.915654   
41                 Astoria              40.768509              -73.915654   
42                 Astoria              40.768509              -73.915654   
43                 Astoria              40.768509              -73.915654   
44                 Astoria              40.768509              -73.915654   
45                 Astoria              40.768509              -73.915654   
46                 Astoria              40.768509              -73.915654   
47                 Astoria              40.768509              -73.915654   
48                 Astoria              40.768509              -73.915654   
49                 Astoria              40.768509              -73.915654   
50                 Astoria              40.768509              -73.915654   
51        

In [25]:
queens_venues.groupby('Venue Category').count()

Neighborhood  Neighborhood Latitude  \
Venue Category                                                                  
Accessories Store                                    2                      2   
Afghan Restaurant                                    2                      2   
Airport Terminal                                     1                      1   
American Restaurant                                 21                     21   
Arepa Restaurant                                     4                      4   
Argentinian Restaurant                               2                      2   
Art Gallery                                          1                      1   
Art Museum                                           1                      1   
Arts & Crafts Store                                  2                      2   
Arts & Entertainment                                 1                      1   
Asian Restaurant                                    18                     18   
Athletics & Sports                                   4                      4   
Auto Workshop                                        1                      1   
Automotive Shop                                      1                      1   
BBQ Joint                                            7                      7   
Bagel Shop                                          21                     21   
Bakery                                              59                     59   
Bank                                                42                     42   
Bar                                                 48                     48   
Baseball Field                                       4                      4   
Basketball Court                                     3                      3   
Bath House                                           1                      1   
Beach                                               26                     26   
Beach Bar                                            1                      1   
Bed & Breakfast                                      1                      1   
Beer Garden                                          3                      3   
Beer Store                                           1                      1   
Bike Rental / Bike Share                             1                      1   
Bike Trail                                           1                      1   
Bistro                                               2                      2   
Board Shop                                           4                      4   
Bookstore                                            1                      1   
Boutique                                             2                      2   
Bowling Alley                                        5                      5   
Brazilian Restaurant                                 4                      4   
Breakfast Spot                                       8                      8   
Brewery                                              6                      6   
Bubble Tea Shop                                     12                     12   
Buffet                                               1                      1   
Building                                             1                      1   
Burger Joint                                         9                      9   
Burrito Place                                        2                      2   
Bus Line                                             2                      2   
Bus Station                                         37                     37   
Bus Stop                                             8                      8   
Business Service                                     2                      2   
Butcher                                              1                      1   
Café                                                24                   

In [26]:
queens_venues.groupby('Venue Category')['Venue'].count().sort_values(ascending=False)

Venue Category
Pizza Place                                 86
Deli / Bodega                               78
Chinese Restaurant                          65
Bakery                                      59
Donut Shop                                  53
Pharmacy                                    52
Bar                                         48
Grocery Store                               43
Italian Restaurant                          42
Bank                                        42
Korean Restaurant                           41
Bus Station                                 37
Mexican Restaurant                          37
Sandwich Place                              36
Supermarket                                 34
Coffee Shop                                 34
Ice Cream Shop                              29
Thai Restaurant                             29
Mobile Phone Shop                           28
Gym / Fitness Center                        28
Latin American Restaurant                   2

In [27]:
import requests
#run function with the Brooklyn borough
brooklyn_venues = getNearbyVenues(names = brooklyn_borough['Neighborhood'],latitudes = brooklyn_borough['Latitude'], longitudes =brooklyn_borough['Longitude'])
brooklyn_venues

Neighborhood  Neighborhood Latitude  \
0                     Bay Ridge              40.625801   
1                     Bay Ridge              40.625801   
2                     Bay Ridge              40.625801   
3                     Bay Ridge              40.625801   
4                     Bay Ridge              40.625801   
5                     Bay Ridge              40.625801   
6                     Bay Ridge              40.625801   
7                     Bay Ridge              40.625801   
8                     Bay Ridge              40.625801   
9                     Bay Ridge              40.625801   
10                    Bay Ridge              40.625801   
11                    Bay Ridge              40.625801   
12                    Bay Ridge              40.625801   
13                    Bay Ridge              40.625801   
14                    Bay Ridge              40.625801   
15                    Bay Ridge              40.625801   
16                    Bay Ridge              40.625801   
17                    Bay Ridge              40.625801   
18                    Bay Ridge              40.625801   
19                    Bay Ridge              40.625801   
20                    Bay Ridge              40.625801   
21                    Bay Ridge              40.625801   
22                    Bay Ridge              40.625801   
23                    Bay Ridge              40.625801   
24                    Bay Ridge              40.625801   
25                    Bay Ridge              40.625801   
26                    Bay Ridge              40.625801   
27                    Bay Ridge              40.625801   
28                    Bay Ridge              40.625801   
29                    Bay Ridge              40.625801   
30                    Bay Ridge              40.625801   
31                    Bay Ridge              40.625801   
32                    Bay Ridge              40.625801   
33                    Bay Ridge              40.625801   
34                    Bay Ridge              40.625801   
35                    Bay Ridge              40.625801   
36                    Bay Ridge              40.625801   
37                    Bay Ridge              40.625801   
38                    Bay Ridge              40.625801   
39                    Bay Ridge              40.625801   
40                    Bay Ridge              40.625801   
41                    Bay Ridge              40.625801   
42                    Bay Ridge              40.625801   
43                    Bay Ridge              40.625801   
44                    Bay Ridge              40.625801   
45                    Bay Ridge              40.625801   
46                    Bay Ridge              40.625801   
47                    Bay Ridge              40.625801   
48                    Bay Ridge              40.625801   
49                    Bay Ridge              40.625801   
50                    Bay Ridge              40.625801   
51                    Bay Ridge              40.625801   
52                    Bay Ridge              40.625801   
53                    Bay Ridge              40.625801   
54                    Bay Ridge              40.625801   
55                    Bay Ridge              40.625801   
56                    Bay Ridge              40.625801   
57                    Bay Ridge              40.625801   
58                    Bay Ridge              40.625801   
59                    Bay Ridge              40.625801   
60                    Bay Ridge              40.625801   
61                    Bay Ridge              40.625801   
62                    Bay Ridge              40.625801   
63                    Bay Ridge              40.625801   
64                    Bay Ridge              40.625801   
65                    Bay Ridge              40.625801   
66                    Bay Ridge              40.625801   
67                    Bay Ridge              40.625801   
68               

In [28]:
brooklyn_venues.groupby('Venue Category').count()

Neighborhood  Neighborhood Latitude  \
Venue Category                                                                  
Adult Boutique                                       1                      1   
Airport Terminal                                     1                      1   
American Restaurant                                 47                     47   
Antique Shop                                        12                     12   
Arepa Restaurant                                     2                      2   
Argentinian Restaurant                               3                      3   
Art Gallery                                         18                     18   
Arts & Crafts Store                                  8                      8   
Arts & Entertainment                                 1                      1   
Asian Restaurant                                    13                     13   
Athletics & Sports                                   4                      4   
Auto Workshop                                        1                      1   
BBQ Joint                                            8                      8   
Baby Store                                           1                      1   
Bagel Shop                                          45                     45   
Bakery                                              64                     64   
Bank                                                28                     28   
Bar                                                 81                     81   
Baseball Field                                       2                      2   
Baseball Stadium                                     1                      1   
Basketball Court                                     2                      2   
Beach                                                9                      9   
Beer Bar                                             4                      4   
Beer Garden                                          7                      7   
Beer Store                                           2                      2   
Big Box Store                                        1                      1   
Bike Rental / Bike Share                             3                      3   
Bike Shop                                            1                      1   
Bistro                                               2                      2   
Board Shop                                           3                      3   
Boat or Ferry                                        2                      2   
Bookstore                                           21                     21   
Boutique                                            12                     12   
Boxing Gym                                           5                      5   
Breakfast Spot                                      17                     17   
Brewery                                              8                      8   
Bridge                                               2                      2   
Bubble Tea Shop                                      6                      6   
Buffet                                               1                      1   
Burger Joint                                        30                     30   
Burrito Place                                        3                      3   
Bus Line                                             1                      1   
Bus Station                                         13                     13   
Bus Stop                                            11                     11   
Business Service                                     2                      2   
Butcher                                              3                      3   
Café                                                53                     53   
Cajun / Creole Restaurant                            3                   

In [29]:
brooklyn_venues.groupby('Venue Category')['Venue'].count().sort_values(ascending=False)

Venue Category
Pizza Place                                 121
Coffee Shop                                  83
Bar                                          81
Deli / Bodega                                72
Italian Restaurant                           69
Bakery                                       64
Chinese Restaurant                           61
Grocery Store                                60
Café                                         53
Mexican Restaurant                           49
Park                                         48
American Restaurant                          47
Ice Cream Shop                               46
Bagel Shop                                   45
Pharmacy                                     44
Sandwich Place                               43
Donut Shop                                   42
Wine Shop                                    37
Caribbean Restaurant                         37
Cocktail Bar                                 37
Yoga Studio              

In [30]:
import requests
#run function with the Staten Island borough
statenisland_venues = getNearbyVenues(names = statenisland_borough['Neighborhood'],latitudes = statenisland_borough['Latitude'], longitudes =statenisland_borough['Longitude'])
statenisland_venues

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           St. George              40.644982              -74.079353   
1           St. George              40.644982              -74.079353   
2           St. George              40.644982              -74.079353   
3           St. George              40.644982              -74.079353   
4           St. George              40.644982              -74.079353   
5           St. George              40.644982              -74.079353   
6           St. George              40.644982              -74.079353   
7           St. George              40.644982              -74.079353   
8           St. George              40.644982              -74.079353   
9           St. George              40.644982              -74.079353   
10          St. George              40.644982              -74.079353   
11          St. George              40.644982              -74.079353   
12          St. George              40.644982              -74.079353   
13          St. George              40.644982              -74.079353   
14          St. George              40.644982              -74.079353   
15          St. George              40.644982              -74.079353   
16          St. George              40.644982              -74.079353   
17          St. George              40.644982              -74.079353   
18          St. George              40.644982              -74.079353   
19          St. George              40.644982              -74.079353   
20          St. George              40.644982              -74.079353   
21          St. George              40.644982              -74.079353   
22        New Brighton              40.640615              -74.087017   
23        New Brighton              40.640615              -74.087017   
24        New Brighton              40.640615              -74.087017   
25        New Brighton              40.640615              -74.087017   
26        New Brighton              40.640615              -74.087017   
27        New Brighton              40.640615              -74.087017   
28        New Brighton              40.640615              -74.087017   
29        New Brighton              40.640615              -74.087017   
30        New Brighton              40.640615              -74.087017   
31        New Brighton              40.640615              -74.087017   
32        New Brighton              40.640615              -74.087017   
33        New Brighton              40.640615              -74.087017   
34           Stapleton              40.626928              -74.077902   
35           Stapleton              40.626928              -74.077902   
36           Stapleton              40.626928              -74.077902   
37           Stapleton              40.626928              -74.077902   
38           Stapleton              40.626928              -74.077902   
39           Stapleton              40.626928              -74.077902   
40           Stapleton              40.626928              -74.077902   
41           Stapleton              40.626928              -74.077902   
42           Stapleton              40.626928              -74.077902   
43           Stapleton              40.626928              -74.077902   
44           Stapleton              40.626928              -74.077902   
45           Stapleton              40.626928              -74.077902   
46           Stapleton              40.626928              -74.077902   
47           Stapleton              40.626928              -74.077902   
48           Stapleton              40.626928              -74.077902   
49           Stapleton              40.626928              -74.077902   
50           Stapleton              40.626928              -74.077902   
51           Stapleton              40.626928              -74.077902   
52           Stapleton              40.626928              -74.077902   
53           Stapleton              40.626928              -74.07790

In [31]:
statenisland_venues.groupby('Venue Category').count()

Neighborhood  Neighborhood Latitude  \
Venue Category                                                                  
Accessories Store                                    2                      2   
American Restaurant                                 16                     16   
Arcade                                               1                      1   
Art Gallery                                          2                      2   
Art Museum                                           1                      1   
Arts & Crafts Store                                  2                      2   
Asian Restaurant                                     2                      2   
Athletics & Sports                                   4                      4   
BBQ Joint                                            2                      2   
Bagel Shop                                          21                     21   
Bakery                                              11                     11   
Bank                                                17                     17   
Bar                                                 13                     13   
Baseball Field                                       5                      5   
Baseball Stadium                                     1                      1   
Basketball Court                                     4                      4   
Beach                                                5                      5   
Beer Bar                                             1                      1   
Big Box Store                                        2                      2   
Board Shop                                           1                      1   
Bookstore                                            3                      3   
Bowling Alley                                        3                      3   
Breakfast Spot                                       3                      3   
Brewery                                              3                      3   
Bridal Shop                                          1                      1   
Burger Joint                                         4                      4   
Bus Line                                             1                      1   
Bus Stop                                            50                     50   
Butcher                                              1                      1   
Café                                                 8                      8   
Cajun / Creole Restaurant                            2                      2   
Campground                                           1                      1   
Caribbean Restaurant                                 2                      2   
Chinese Restaurant                                  19                     19   
Clothing Store                                       2                      2   
Coffee Shop                                         13                     13   
Comedy Club                                          1                      1   
Construction & Landscaping                           4                      4   
Convenience Store                                    8                      8   
Cosmetics Shop                                      13                     13   
Dance Studio                                         1                      1   
Deli / Bodega                                       39                     39   
Department Store                                     1                      1   
Dessert Shop                                         5                      5   
Dim Sum Restaurant                                   1                      1   
Diner                                                9                      9   
Discount Store                                       7                      7   
Dog Run                                              1                   

In [32]:
statenisland_venues.groupby('Venue Category')['Venue'].count().sort_values(ascending=False)

Venue Category
Pizza Place                                 57
Bus Stop                                    50
Italian Restaurant                          45
Deli / Bodega                               39
Bagel Shop                                  21
Pharmacy                                    21
Chinese Restaurant                          19
Grocery Store                               17
Bank                                        17
Sandwich Place                              17
Donut Shop                                  16
American Restaurant                         16
Mexican Restaurant                          13
Cosmetics Shop                              13
Coffee Shop                                 13
Park                                        13
Bar                                         13
Restaurant                                  12
Train Station                               12
Sushi Restaurant                            12
Supermarket                                 1

In [33]:
import requests
#run function with the Manhattan borough
manhattan_venues = getNearbyVenues(names = manhattan_borough['Neighborhood'],latitudes = manhattan_borough['Latitude'], longitudes =manhattan_borough['Longitude'])
manhattan_venues

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0             Marble Hill              40.876551              -73.910660   
1             Marble Hill              40.876551              -73.910660   
2             Marble Hill              40.876551              -73.910660   
3             Marble Hill              40.876551              -73.910660   
4             Marble Hill              40.876551              -73.910660   
5             Marble Hill              40.876551              -73.910660   
6             Marble Hill              40.876551              -73.910660   
7             Marble Hill              40.876551              -73.910660   
8             Marble Hill              40.876551              -73.910660   
9             Marble Hill              40.876551              -73.910660   
10            Marble Hill              40.876551              -73.910660   
11            Marble Hill              40.876551              -73.910660   
12            Marble Hill              40.876551              -73.910660   
13            Marble Hill              40.876551              -73.910660   
14            Marble Hill              40.876551              -73.910660   
15            Marble Hill              40.876551              -73.910660   
16            Marble Hill              40.876551              -73.910660   
17            Marble Hill              40.876551              -73.910660   
18            Marble Hill              40.876551              -73.910660   
19            Marble Hill              40.876551              -73.910660   
20            Marble Hill              40.876551              -73.910660   
21            Marble Hill              40.876551              -73.910660   
22            Marble Hill              40.876551              -73.910660   
23            Marble Hill              40.876551              -73.910660   
24            Marble Hill              40.876551              -73.910660   
25              Chinatown              40.715618              -73.994279   
26              Chinatown              40.715618              -73.994279   
27              Chinatown              40.715618              -73.994279   
28              Chinatown              40.715618              -73.994279   
29              Chinatown              40.715618              -73.994279   
30              Chinatown              40.715618              -73.994279   
31              Chinatown              40.715618              -73.994279   
32              Chinatown              40.715618              -73.994279   
33              Chinatown              40.715618              -73.994279   
34              Chinatown              40.715618              -73.994279   
35              Chinatown              40.715618              -73.994279   
36              Chinatown              40.715618              -73.994279   
37              Chinatown              40.715618              -73.994279   
38              Chinatown              40.715618              -73.994279   
39              Chinatown              40.715618              -73.994279   
40              Chinatown              40.715618              -73.994279   
41              Chinatown              40.715618              -73.994279   
42              Chinatown              40.715618              -73.994279   
43              Chinatown              40.715618              -73.994279   
44              Chinatown              40.715618              -73.994279   
45              Chinatown              40.715618              -73.994279   
46              Chinatown              40.715618              -73.994279   
47              Chinatown              40.715618              -73.994279   
48              Chinatown              40.715618              -73.994279   
49              Chinatown              40.715618              -73.994279   
50              Chinatown              40.715618              -73.994279   
51              Chinatown              40.715618             

In [34]:
manhattan_venues.groupby('Venue Category').count()

Neighborhood  Neighborhood Latitude  \
Venue Category                                                                  
Accessories Store                                    4                      4   
Adult Boutique                                       2                      2   
Afghan Restaurant                                    1                      1   
African Restaurant                                   3                      3   
American Restaurant                                 75                     75   
Animal Shelter                                       1                      1   
Antique Shop                                         2                      2   
Arcade                                               1                      1   
Arepa Restaurant                                     3                      3   
Argentinian Restaurant                               4                      4   
Art Gallery                                         29                     29   
Art Museum                                           3                      3   
Arts & Crafts Store                                  3                      3   
Asian Restaurant                                    13                     13   
Athletics & Sports                                   3                      3   
Auditorium                                           1                      1   
Australian Restaurant                                4                      4   
Austrian Restaurant                                  2                      2   
Auto Workshop                                        1                      1   
BBQ Joint                                            5                      5   
Baby Store                                           1                      1   
Bagel Shop                                          22                     22   
Bakery                                              79                     79   
Bank                                                 4                      4   
Bar                                                 59                     59   
Baseball Field                                       1                      1   
Basketball Court                                     2                      2   
Beer Bar                                             8                      8   
Beer Garden                                          4                      4   
Beer Store                                           4                      4   
Big Box Store                                        2                      2   
Bike Rental / Bike Share                             1                      1   
Bike Shop                                            2                      2   
Bike Trail                                           1                      1   
Bistro                                               3                      3   
Board Shop                                           1                      1   
Boat or Ferry                                        5                      5   
Bookstore                                           27                     27   
Boutique                                            31                     31   
Boxing Gym                                           4                      4   
Brazilian Restaurant                                 2                      2   
Breakfast Spot                                       7                      7   
Bridal Shop                                          3                      3   
Bubble Tea Shop                                     12                     12   
Building                                             6                      6   
Burger Joint                                        31                     31   
Burrito Place                                        4                      4   
Bus Line                                             1                   

In [35]:
manhattan_venues.groupby('Venue Category')['Venue'].count().sort_values(ascending=False)

Venue Category
Italian Restaurant                          133
Coffee Shop                                 126
Bakery                                       79
American Restaurant                          75
Café                                         74
Pizza Place                                  70
Hotel                                        68
Park                                         63
Gym                                          59
Mexican Restaurant                           59
Bar                                          59
French Restaurant                            57
Gym / Fitness Center                         55
Cocktail Bar                                 54
Spa                                          49
Chinese Restaurant                           47
Sushi Restaurant                             47
Sandwich Place                               45
Japanese Restaurant                          42
Clothing Store                               42
Wine Shop                

## Manhattan

In [36]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_data.head()

Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688

In [37]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Manhattan are 40.7900869, -73.9598295.


In [38]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhattan_data['Latitude'], manhattan_data['Longitude'], manhattan_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)  
    
map_manhattan

In [39]:
CLIENT_ID = 'YXEOOWTLRQO5OH3VPQQGFL3L4N4MKFNALBHUHMFUWCUBRFFI' # your Foursquare ID
CLIENT_SECRET = 'QXTGWBWIGBDS15ZZAIGG5BXQNPAQMPC12RR2IEQKXFXEBR2S' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: YXEOOWTLRQO5OH3VPQQGFL3L4N4MKFNALBHUHMFUWCUBRFFI
CLIENT_SECRET:QXTGWBWIGBDS15ZZAIGG5BXQNPAQMPC12RR2IEQKXFXEBR2S


In [40]:
# convert cateogorical value into binary value using one hot coding
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")
manhattan_onehot.head()
# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood']

In [41]:
manhattan_onehot.head()

Accessories Store  Adult Boutique  Afghan Restaurant  African Restaurant  \
0                  0               0                  0                   0   
1                  0               0                  0                   0   
2                  0               0                  0                   0   
3                  0               0                  0                   0   
4                  0               0                  0                   0   

   American Restaurant  Animal Shelter  Antique Shop  Arcade  \
0                    0               0             0       0   
1                    0               0             0       0   
2                    0               0             0       0   
3                    0               0             0       0   
4                    0               0             0       0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0                 0                       0            0           0   
1                 0                       0            0           0   
2                 0                       0            0           0   
3                 0                       0            0           0   
4                 0                       0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auditorium  \
0                    0                 0                   0           0   
1                    0                 0                   0           0   
2                    0                 0                   0           0   
3                    0                 0                   0           0   
4                    0                 0                   0           0   

   Australian Restaurant  Austrian Restaurant  Auto Workshop  BBQ Joint  \
0                      0                    0              0          0   
1                      0                    0              0          0   
2                      0                    0              0          0   
3                      0                    0              0          0   
4                      0                    0              0          0   

   Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Field  \
0           0           0       0     0    0               0   
1           0           0       0     0    0               0   
2           0           0       0     0    0               0   
3           0           0       0     0    0               0   
4           0           0       0     0    0               0   

   Basketball Court  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                 0         0            0           0              0   
1                 0         0            0           0              0   
2                 0         0            0           0              0   
3                 0         0            0           0              0   
4                 0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  Board Shop  \
0                         0          0           0       0           0   
1                         0          0           0       0           0   
2                         0          0           0       0           0   
3                         0          0           0       0           0   
4                         0          0           0       0           0   

   Boat or Ferry  Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  \
0              0          0         0           0                     0   
1              0          0         0           0                     0   
2              0          0         0           0                     0   
3              0          0         0           0                     0   
4              0          0         0           0                     0   

   Breakfast Spot  Bridal Shop  Bubble Tea Shop  Building  Burger Joint  \
0      

Find mean frequency of occurrence of each category

In [42]:
manhattan_grouped = manhattan_onehot.groupby("Neighborhood").mean().reset_index()
manhattan_grouped
manhattan_grouped.shape

(40, 332)

In [43]:
manhattan_grouped

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Battery Park City           0.000000            0.00               0.00   
1         Carnegie Hill           0.000000            0.00               0.00   
2        Central Harlem           0.000000            0.00               0.00   
3               Chelsea           0.000000            0.00               0.00   
4             Chinatown           0.000000            0.00               0.00   
5          Civic Center           0.000000            0.00               0.00   
6               Clinton           0.000000            0.00               0.00   
7           East Harlem           0.000000            0.00               0.00   
8          East Village           0.000000            0.00               0.00   
9    Financial District           0.010000            0.00               0.00   
10             Flatiron           0.000000            0.00               0.00   
11             Gramercy           0.000000            0.00               0.00   
12    Greenwich Village           0.000000            0.00               0.00   
13     Hamilton Heights           0.000000            0.00               0.00   
14         Hudson Yards           0.000000            0.00               0.00   
15               Inwood           0.000000            0.00               0.00   
16           Lenox Hill           0.000000            0.00               0.01   
17       Lincoln Square           0.000000            0.00               0.00   
18         Little Italy           0.000000            0.00               0.00   
19      Lower East Side           0.000000            0.00               0.00   
20     Manhattan Valley           0.000000            0.00               0.00   
21       Manhattanville           0.000000            0.00               0.00   
22          Marble Hill           0.000000            0.00               0.00   
23              Midtown           0.000000            0.00               0.00   
24        Midtown South           0.000000            0.00               0.00   
25  Morningside Heights           0.000000            0.00               0.00   
26          Murray Hill           0.000000            0.00               0.00   
27                 Noho           0.000000            0.01               0.00   
28     Roosevelt Island           0.000000            0.00               0.00   
29                 Soho           0.000000            0.00               0.00   
30      Stuyvesant Town           0.000000            0.00               0.00   
31         Sutton Place           0.000000            0.01               0.00   
32              Tribeca           0.000000            0.00               0.00   
33           Tudor City           0.000000            0.00               0.00   
34           Turtle Bay           0.000000            0.00               0.00   
35      Upper East Side           0.000000            0.00               0.00   
36      Upper West Side           0.010000            0.00               0.00   
37   Washington Heights           0.011765            0.00               0.00   
38         West Village           0.010000            0.00               0.00   
39            Yorkville           0.000000            0.00               0.00   

    African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0             0.000000             0.010204            0.00          0.00   
1             0.000000             0.010000            0.00          0.00   
2             0.069767             0.046512            0.00          0.00   
3             0.000000             0.030000            0.00          0.00   
4             0.000000             0.040000            0.00          0.00   
5             0.000000             0.030000            0.00          0.01   
6             0.000000             0.040000            0.00          0.00   
7             0.000000             0.000000            0.00          0.00

In [44]:
# print each neighbourhood along with the top 5 most common venues
num_top_venues =5
for hood in manhattan_grouped['Neighborhood']:
    print("---"+hood+"---")
    temp = manhattan_grouped[manhattan_grouped["Neighborhood"] ==hood].T.reset_index()
    temp.columns =['venue','freq']
    temp=temp.iloc[1:]
    temp['freq']= temp['freq'].astype(float)
    temp=temp.round({'freq':2})
    print(temp.sort_values('freq', ascending = False).reset_index(drop=True).head(num_top_venues))
    print('\n')

---Battery Park City---
            venue  freq
0     Coffee Shop  0.07
1            Park  0.07
2           Hotel  0.05
3             Gym  0.04
4  Clothing Store  0.03


---Carnegie Hill---
            venue  freq
0     Pizza Place  0.06
1     Coffee Shop  0.05
2             Bar  0.04
3  Cosmetics Shop  0.04
4            Café  0.04


---Central Harlem---
                  venue  freq
0    African Restaurant  0.07
1    Chinese Restaurant  0.05
2  Gym / Fitness Center  0.05
3   American Restaurant  0.05
4    Seafood Restaurant  0.05


---Chelsea---
                venue  freq
0         Coffee Shop  0.07
1  Italian Restaurant  0.05
2      Ice Cream Shop  0.05
3              Bakery  0.04
4           Nightclub  0.04


---Chinatown---
                   venue  freq
0     Chinese Restaurant  0.10
1     Dim Sum Restaurant  0.04
2    American Restaurant  0.04
3  Vietnamese Restaurant  0.04
4           Cocktail Bar  0.04


---Civic Center---
                  venue  freq
0  Gym / Fitness Center 

In [45]:
#sort venues in descending order
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [46]:
import numpy as np 
# put into a pandas dataframe
# write a function to sort venues in descending order
def sort_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    return row_categories_sorted.index.values[0:num_top_venues]
# create the new data frame and display the top 10 venues for each neighbourhood
num_top_venues =5
indicators =['st', 'nd','rd']
# create columns according to number of top venues
columns =['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{}Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))
# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame (columns =columns)
neighborhoods_venues_sorted['Neighborhood'] = manhattan_grouped['Neighborhood']
for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind,1:] = sort_venues(manhattan_grouped.iloc[ind, :], num_top_venues)
neighborhoods_venues_sorted.head()

Neighborhood 1stMost Common Venue 2ndMost Common Venue  \
0  Battery Park City          Coffee Shop                 Park   
1      Carnegie Hill          Pizza Place          Coffee Shop   
2     Central Harlem   African Restaurant       Cosmetics Shop   
3            Chelsea          Coffee Shop       Ice Cream Shop   
4          Chinatown   Chinese Restaurant   Dim Sum Restaurant   

  3rdMost Common Venue 4th Most Common Venue  5th Most Common Venue  
0                Hotel                   Gym     Italian Restaurant  
1                  Bar                  Café         Cosmetics Shop  
2  American Restaurant     French Restaurant   Gym / Fitness Center  
3   Italian Restaurant             Nightclub                 Bakery  
4         Cocktail Bar   American Restaurant  Vietnamese Restaurant

Determine number of Caribbean restaurants, bus stops, farmers markets and monuments/landmarks based on investment criteria

In [62]:
manhattan_grouped[['Neighborhood','Caribbean Restaurant','Bus Stop','Farmers Market','Monument / Landmark']]

Neighborhood  Caribbean Restaurant  Bus Stop  Farmers Market  \
0     Battery Park City              0.000000  0.000000        0.000000   
1         Carnegie Hill              0.000000  0.000000        0.000000   
2        Central Harlem              0.023256  0.000000        0.000000   
3               Chelsea              0.000000  0.000000        0.000000   
4             Chinatown              0.000000  0.000000        0.000000   
5          Civic Center              0.000000  0.000000        0.000000   
6               Clinton              0.000000  0.000000        0.000000   
7           East Harlem              0.000000  0.000000        0.000000   
8          East Village              0.010000  0.000000        0.010000   
9    Financial District              0.000000  0.000000        0.010000   
10             Flatiron              0.000000  0.000000        0.000000   
11             Gramercy              0.000000  0.000000        0.000000   
12    Greenwich Village              0.020000  0.000000        0.000000   
13     Hamilton Heights              0.032787  0.000000        0.000000   
14         Hudson Yards              0.000000  0.000000        0.000000   
15               Inwood              0.017544  0.000000        0.017544   
16           Lenox Hill              0.000000  0.000000        0.000000   
17       Lincoln Square              0.000000  0.000000        0.000000   
18         Little Italy              0.000000  0.000000        0.000000   
19      Lower East Side              0.000000  0.000000        0.000000   
20     Manhattan Valley              0.016949  0.000000        0.016949   
21       Manhattanville              0.000000  0.023256        0.000000   
22          Marble Hill              0.000000  0.000000        0.000000   
23              Midtown              0.000000  0.000000        0.000000   
24        Midtown South              0.000000  0.000000        0.000000   
25  Morningside Heights              0.000000  0.000000        0.024390   
26          Murray Hill              0.000000  0.000000        0.000000   
27                 Noho              0.000000  0.000000        0.000000   
28     Roosevelt Island              0.000000  0.000000        0.043478   
29                 Soho              0.000000  0.000000        0.000000   
30      Stuyvesant Town              0.000000  0.000000        0.052632   
31         Sutton Place              0.000000  0.000000        0.000000   
32              Tribeca              0.000000  0.000000        0.000000   
33           Tudor City              0.000000  0.000000        0.000000   
34           Turtle Bay              0.000000  0.000000        0.010000   
35      Upper East Side              0.000000  0.000000        0.000000   
36      Upper West Side              0.000000  0.000000        0.000000   
37   Washington Heights              0.011765  0.000000        0.000000   
38         West Village              0.000000  0.000000        0.000000   
39            Yorkville              0.000000  0.000000        0.010000   

    Monument / Landmark  
0              0.010204  
1              0.000000  
2              0.000000  
3              0.000000  
4              0.000000  
5              0.010000  
6              0.000000  
7              0.000000  
8              0.000000  
9              0.020000  
10             0.000000  
11             0.000000  
12             0.000000  
13             0.000000  
14             0.000000  
15             0.000000  
16             0.000000  
17             0.000000  
18             0.000000  
19             0.000000  
20             0.000000  
21             0.000000  
22             0.000000  
23             0.000000  
24             0.000000  
25             0.000000  
26             0.000000  
27             0.000000  
28             0.000000  
29             0.000000  
30             0.000000  
31             0.000000  
32             0.000000  
33             0.000000  
34             0.000000  

In [49]:
X=manhattan_grouped.drop(['Neighborhood','Caribbean Restaurant'],axis=1)
y=manhattan_grouped['Caribbean Restaurant']

## **Cluster properties by venue category**

In [50]:
import random # library for random number generation
import numpy as np # library for vectorized computation
import pandas as pd # library to process data as dataframes

import matplotlib.pyplot as plt # plotting library
# backend for rendering plots within the browser
%matplotlib inline 

from sklearn.cluster import KMeans 
from sklearn.datasets.samples_generator import make_blobs

print('Libraries imported.')

Libraries imported.


In [51]:
# set number of clusters
kclusters = 3

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 1, 2, 2, 2, 2, 2, 1, 2, 2], dtype=int32)

In [52]:
# add clustering labels 
neighborhoods_venues_sorted.insert(0,'Labels', kmeans.labels_)
# merge data of toronto,  venues, and kmeans labels
manhattan_merged = manhattan_borough
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on ='Neighborhood')
manhattan_merged.head()

Borough        Neighborhood   Latitude  Longitude  Labels  \
0  Manhattan         Marble Hill  40.876551 -73.910660       1   
1  Manhattan           Chinatown  40.715618 -73.994279       2   
2  Manhattan  Washington Heights  40.851903 -73.936900       1   
3  Manhattan              Inwood  40.867684 -73.921210       1   
4  Manhattan    Hamilton Heights  40.823604 -73.949688       1   

  1stMost Common Venue 2ndMost Common Venue 3rdMost Common Venue  \
0          Coffee Shop       Discount Store       Sandwich Place   
1   Chinese Restaurant   Dim Sum Restaurant         Cocktail Bar   
2                 Café               Bakery        Grocery Store   
3   Mexican Restaurant                 Café               Lounge   
4   Mexican Restaurant          Coffee Shop          Pizza Place   

  4th Most Common Venue      5th Most Common Venue  
0        Tennis Stadium                        Gym  
1   American Restaurant      Vietnamese Restaurant  
2     Mobile Phone Shop  Latin American Restaurant  
3           Pizza Place                       Park  
4                  Café                Yoga Studio

In [56]:
# visualize the resulting cluster
# create map
address ='Manhattan, NY'
geolocator = Nominatim(user_agent="foursquare_agent")
location = geolocator.geocode(address)
latitude = location.latitude
longitude =location.longitude
map_clusters = folium.Map(location =[latitude, longitude], zoom_start=11)
# set color scheme in clusters
x= np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0,1,len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
# add markers to the map
marker_colors=[]
for lat, lon, poil, cluster in zip(manhattan_merged['Latitude'],manhattan_merged['Longitude'], manhattan_merged['Neighborhood'], manhattan_merged['Labels'] ):
    label = folium.Popup(str(poil)+'Cluster'+str(cluster), parse_html=True)
    folium.CircleMarker([lat,lon],radius =5,popup=label, color =rainbow[cluster-1], fill=True,
                       fill_color =rainbow[cluster-1], fill_opacity=0.7).add_to(map_clusters)
map_clusters

## Examine the clusters

In [57]:
manhattan_merged.loc[manhattan_merged['Labels'] == 0, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1stMost Common Venue 2ndMost Common Venue  \
37  Stuyvesant Town                  Bar           Playground   

   3rdMost Common Venue 4th Most Common Venue 5th Most Common Venue  
37                 Park           Gas Station           Pet Service

In [58]:
manhattan_merged.loc[manhattan_merged['Labels'] == 1, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood 1stMost Common Venue 2ndMost Common Venue  \
0           Marble Hill          Coffee Shop       Discount Store   
2    Washington Heights                 Café               Bakery   
3                Inwood   Mexican Restaurant                 Café   
4      Hamilton Heights   Mexican Restaurant          Coffee Shop   
7           East Harlem   Mexican Restaurant               Bakery   
11     Roosevelt Island       Sandwich Place                 Park   
20      Lower East Side                 Café          Art Gallery   
25     Manhattan Valley          Coffee Shop          Pizza Place   
26  Morningside Heights          Coffee Shop  American Restaurant   
30        Carnegie Hill          Pizza Place          Coffee Shop   
36           Tudor City   Mexican Restaurant                 Park   

   3rdMost Common Venue      4th Most Common Venue      5th Most Common Venue  
0        Sandwich Place             Tennis Stadium                        Gym  
2         Grocery Store          Mobile Phone Shop  Latin American Restaurant  
3                Lounge                Pizza Place                       Park  
4           Pizza Place                       Café                Yoga Studio  
7         Deli / Bodega  Latin American Restaurant                Pizza Place  
11  Japanese Restaurant                Pizza Place                   Bus Line  
20          Coffee Shop        Japanese Restaurant             Sandwich Place  
25   Mexican Restaurant          French Restaurant          Indian Restaurant  
26                 Park                  Bookstore                 Food Truck  
30                  Bar                       Café             Cosmetics Shop  
36     Greek Restaurant                       Café                      Hotel

In [59]:
manhattan_merged.loc[manhattan_merged['Labels'] == 2, manhattan_merged.columns[[1] + list(range(5, manhattan_merged.shape[1]))]]

Neighborhood  1stMost Common Venue 2ndMost Common Venue  \
1            Chinatown    Chinese Restaurant   Dim Sum Restaurant   
5       Manhattanville           Coffee Shop                 Park   
6       Central Harlem    African Restaurant       Cosmetics Shop   
8      Upper East Side    Italian Restaurant              Exhibit   
9            Yorkville                   Bar                  Gym   
10          Lenox Hill    Italian Restaurant          Coffee Shop   
12     Upper West Side    Italian Restaurant                  Bar   
13      Lincoln Square               Theater                 Café   
14             Clinton               Theater  American Restaurant   
15             Midtown                 Hotel       Clothing Store   
16         Murray Hill                 Hotel  Japanese Restaurant   
17             Chelsea           Coffee Shop       Ice Cream Shop   
18   Greenwich Village    Italian Restaurant     Sushi Restaurant   
19        East Village                   Bar             Wine Bar   
21             Tribeca    Italian Restaurant                 Park   
22        Little Italy                Bakery                 Café   
23                Soho        Clothing Store             Boutique   
24        West Village    Italian Restaurant       Cosmetics Shop   
27            Gramercy    Italian Restaurant          Pizza Place   
28   Battery Park City           Coffee Shop                 Park   
29  Financial District           Coffee Shop           Steakhouse   
31                Noho    Italian Restaurant    French Restaurant   
32        Civic Center  Gym / Fitness Center   Italian Restaurant   
33       Midtown South     Korean Restaurant                Hotel   
34        Sutton Place  Gym / Fitness Center   Italian Restaurant   
35          Turtle Bay      Sushi Restaurant                Hotel   
38            Flatiron           Yoga Studio  American Restaurant   
39        Hudson Yards           Coffee Shop                Hotel   

       3rdMost Common Venue   4th Most Common Venue  \
1              Cocktail Bar     American Restaurant   
5          Sushi Restaurant      Italian Restaurant   
6       American Restaurant       French Restaurant   
8               Coffee Shop             Art Gallery   
9               Coffee Shop      Italian Restaurant   
10         Sushi Restaurant    Gym / Fitness Center   
12              Coffee Shop       Indian Restaurant   
13       Italian Restaurant            Concert Hall   
14                    Hotel      Italian Restaurant   
15                  Theater            Cocktail Bar   
16              Coffee Shop      Italian Restaurant   
17       Italian Restaurant               Nightclub   
18        French Restaurant          Clothing Store   
19       Mexican Restaurant          Ice Cream Shop   
21                     Café     American Restaurant   
22       Seafood Restaurant          Sandwich Place   
23            Women's Store             Men's Store   
24  New American Restaurant                Wine Bar   
27      American Restaurant              Bagel Shop   
28                    Hotel                     Gym   
29                    Hotel      Italian Restaurant   
31             Cocktail Bar             Coffee Shop   
32                   Bakery             Coffee Shop   
33                Hotel Bar     Japanese Restaurant   
34        Indian Restaurant  Furniture / Home Store   
35               Steakhouse      Italian Restaurant   
38                      Gym    Gym / Fitness Center   
39       Italian Restaurant                 Theater   

            5th Most Common Venue  
1           Vietnamese Restaurant  
5              Mexican Restaurant  
6            Gym / Fitness Center  
8                       Juice Bar  
9                     Pizza Place  
10                    Pizza Place  
12                       Wine Bar  
13           Gym / Fitness Center  
14           Gym / Fitness Center  
15            American Restaurant  
16              